In [123]:
import json
import re
import pandas as pd
import requests
import scrapy



In [124]:
# Adds the User-Agent becase goheels blockes the python agent.
base_url = 'http://goheels.com'
url = base_url + '/roster.aspx?path=mbball'
headers = {'User-Agent': 'UNC Journo Class'}
resp = requests.get(url, headers={'User-Agent': 'UNC Journo Class'},)


In [125]:
body_bytes = resp.content

body_str = body_bytes.decode('utf-8')

In [126]:
#sel = scrapy.Selector(text=body_str)
sel = scrapy.Selector(text=body_str)

In [127]:
#selects the first table using [index]
table = sel.css('table')[0]
table

<Selector xpath='descendant-or-self::table' data='<table class="sidearm-table sidearm-tabl'>

In [128]:
table.css('tr') # Get all the tr elements within the table
table.css('tr')[0] # Get the first tr element within the table using the pythonic index
table.css('tr')[0].css('th') # Get all the th elements from within the first tr
table.css('tr:nth-child(1) th') # Get all the th elements from the first tr element within the table using CSS selector
# !!!! Note the table on the page has a header and a footer and there will be TWO sets of tr's with th's

[<Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' 

In [129]:
table.css('tr:nth-child(1) th')

[<Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' data='<th scope="col" class="text-left text-up'>,
 <Selector xpath='descendant-or-self::tr[count(preceding-sibling::*) = 0]/descendant-or-self::*/th' 

In [130]:
table.css('tr')[0].css('th').xpath('string()') 

[<Selector xpath='string()' data='No.'>,
 <Selector xpath='string()' data='Name'>,
 <Selector xpath='string()' data='Pos.'>,
 <Selector xpath='string()' data='Ht.'>,
 <Selector xpath='string()' data='Wt.'>,
 <Selector xpath='string()' data='Yr.'>,
 <Selector xpath='string()' data='Hometown / High School'>]

In [131]:
table.css('tr')[0].css('th').xpath('string()').extract()

['No.', 'Name', 'Pos.', 'Ht.', 'Wt.', 'Yr.', 'Hometown / High School']

In [132]:
col_names = table.css('tr:nth-child(1) th').xpath('string()').extract()

In [133]:
col_names

['No.', 'Name', 'Pos.', 'Ht.', 'Wt.', 'Yr.', 'Hometown / High School']

In [134]:
other_rows = table.css('tr:not(:nth-child(1))')

In [135]:
other_rows

[<Selector xpath='descendant-or-self::tr[not(count(preceding-sibling::*) = 0)]' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr[not(count(preceding-sibling::*) = 0)]' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr[not(count(preceding-sibling::*) = 0)]' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr[not(count(preceding-sibling::*) = 0)]' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr[not(count(preceding-sibling::*) = 0)]' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr[not(count(preceding-sibling::*) = 0)]' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr[not(count(preceding-sibling::*) = 0)]' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr[not(count(preceding-sibling::*) = 0

In [136]:
# my starting point for just getting the information from the rows
by_player_num = {}
for row in other_rows:
    player_num = row.css('td')[0].xpath('string()').extract()[0]
    player_name = row.css('td')[1].xpath('string()').extract()[0]
    player_position = row.css('td')[2].xpath('string()').extract()[0]
    player_num_data = []
    player_name_data = []
    
    by_player_num[player_num] = player_name, player_position 


In [137]:
by_player_num

{'1': ('Theo Pinson', 'F/G'),
 '11': ('Shea Rush', 'F'),
 '13': ('Cameron Johnson', 'G'),
 '14': ('Kane Ma', 'G'),
 '15': ('Garrison Brooks', 'F'),
 '2': ('Joel Berry II', 'G'),
 '21': ('Sterling Manley', 'F'),
 '22': ('Walker Miller', 'F'),
 '24': ('Kenny Williams', 'G'),
 '25': ('Aaron Rohlman', 'F'),
 '3': ('Andrew Platek', 'G'),
 '30': ('K.J. Smith', 'G'),
 '32': ('Luke Maye', 'F'),
 '4': ('Brandon Robinson', 'G'),
 '42': ('Brandon Huffman', 'F')}

In [138]:

#populate all the data to the object organized by number
by_player_num = {}
player_data = []
for row in other_rows:
    
    player_num = row.css('td')[0].xpath('string()').extract()[0]
    player_name = row.css('td')[1].xpath('string()').extract()[0]
    # get the second cell, then the link, then just the href
    link = row.css('td')[1]
    link = link.css('a')
    player_href= link.xpath('@href').extract()
    player_position = row.css('td')[2].xpath('string()').extract()[0]
    player_num_data = []
    player_data = {
        "name": player_name,
        "position": player_position,
        "href": player_href[0],
    }
    
    
    
#     player_data.append({
#             "name": player_name,
#             "position": player_position,
#             "href": player_href[0],
#         })
    
    by_player_num[player_num] = player_data 
   

In [139]:
by_player_num

{'1': {'href': '/roster.aspx?rp_id=13515',
  'name': 'Theo Pinson',
  'position': 'F/G'},
 '11': {'href': '/roster.aspx?rp_id=13518',
  'name': 'Shea Rush',
  'position': 'F'},
 '13': {'href': '/roster.aspx?rp_id=13525',
  'name': 'Cameron Johnson',
  'position': 'G'},
 '14': {'href': '/roster.aspx?rp_id=14170',
  'name': 'Kane Ma',
  'position': 'G'},
 '15': {'href': '/roster.aspx?rp_id=13522',
  'name': 'Garrison Brooks',
  'position': 'F'},
 '2': {'href': '/roster.aspx?rp_id=13508',
  'name': 'Joel Berry II',
  'position': 'G'},
 '21': {'href': '/roster.aspx?rp_id=13526',
  'name': 'Sterling Manley',
  'position': 'F'},
 '22': {'href': '/roster.aspx?rp_id=13527',
  'name': 'Walker Miller',
  'position': 'F'},
 '24': {'href': '/roster.aspx?rp_id=13520',
  'name': 'Kenny Williams',
  'position': 'G'},
 '25': {'href': '/roster.aspx?rp_id=13517',
  'name': 'Aaron Rohlman',
  'position': 'F'},
 '3': {'href': '/roster.aspx?rp_id=13528',
  'name': 'Andrew Platek',
  'position': 'G'},
 '30'

In [140]:
# now get data from secondary, profile page
for player in list(by_player_num.values()):
    new_url = 'http://goheels.com' + player["href"]
    resp = requests.get(new_url, headers={'User-Agent': 'UNC Journo Class'},)
    content = resp.content.decode('utf-8')
    sel = scrapy.Selector(text=content)
    #selects the image url
    player_image = sel.css('.sidearm-roster-player-image img').xpath("@src").extract()[0]
    # selects the biography
    player_bio = sel.css('#sidearm-roster-player-bio').xpath('string()').extract()[0]
    #player_data = by_player_num[player_num]


    player["image"] = player_image
    #player["bio"] = player_bio
        
    
    #by_player_num[player_num] = player_data
    


In [141]:
by_player_num


{'1': {'href': '/roster.aspx?rp_id=13515',
  'image': '/images/2017/9/12/Pinson_Theo_mb_2017_23.jpg?width=300',
  'name': 'Theo Pinson',
  'position': 'F/G'},
 '11': {'href': '/roster.aspx?rp_id=13518',
  'image': '/images/2017/12/22/Rush_Shea.jpg?width=300',
  'name': 'Shea Rush',
  'position': 'F'},
 '13': {'href': '/roster.aspx?rp_id=13525',
  'image': '/images/2017/9/12/Johnson_Cameron_mb_2017_130.jpg?width=300',
  'name': 'Cameron Johnson',
  'position': 'G'},
 '14': {'href': '/roster.aspx?rp_id=14170',
  'image': '/images/2017/12/22/Ma_Kane.jpg?width=300',
  'name': 'Kane Ma',
  'position': 'G'},
 '15': {'href': '/roster.aspx?rp_id=13522',
  'image': '/images/2017/9/12/Brooks_Garrison_mb_2017_221.jpg?width=300',
  'name': 'Garrison Brooks',
  'position': 'F'},
 '2': {'href': '/roster.aspx?rp_id=13508',
  'image': '/images/2017/9/12/Berry_Joel_mb_2017_59.jpg?width=300',
  'name': 'Joel Berry II',
  'position': 'G'},
 '21': {'href': '/roster.aspx?rp_id=13526',
  'image': '/images/2

In [142]:
# Create a regular expression to find javascript objects on the page being passed to a function call...

# There is JS on the page that looks like
# $.getJSON("/services/responsive-roster-bio.ashx", { type: 'stats', rp_id: 9450, path: 'baseball', year: 2017, player_id: 3759 }
# and we want the object:
# { type: 'stats', rp_id: 9450, path: 'baseball', year: 2017, player_id: 3759 }
# This pattern will match and capture anything between curly braces following the ashx url
js_obj_rx = re.compile(r'.*?responsive-roster-bio\.ashx.*?({.*?})')



# now get data from secondary, profile page
for player in list(by_player_num.values()):
    new_url = 'http://goheels.com' + player["href"]
    resp = requests.get(new_url, headers={'User-Agent': 'UNC Journo Class'},)
    content = resp.content.decode('utf-8')
    sel = scrapy.Selector(text=content)
    #selects the image url
    player_image = sel.css('.sidearm-roster-player-image img').xpath("@src").extract()[0]
    # selects the biography
    player_bio = sel.css('#sidearm-roster-player-bio').xpath('string()').extract()[0]

    player["image"] = player_image
    #player["bio"] = player_bio
    
    # Now we know what leads up to the content we're looking for so 
    # we split the text content some token that preceeds our 
    # regex to reduce the text size
    parts = content.split('$.getJSON("/services/')[1:]
    
    # Now we run our regular expression on the joined 
    # parts (put them back in to a single string)
    # and capture the JS objects
    captured = js_obj_rx.findall(''.join(parts))
    
    # Turn it in to valid json by splitting everything apart
    clean_objs = []
    for obj_str in captured:
        # We only want the stats object...
        if 'stats' not in obj_str:
            continue

        # Remove the braces
        obj_str = obj_str.replace('{', '').replace('}', '')
        # Remove the quotes
        obj_str = obj_str.replace("'", '').replace('"', '')
        # Split apart on commas
        obj_pairs = obj_str.split(',')
        # Now it looks like [" type: related", " rp_id: 9450", ...]
        # So we need to wrap everything in quotes to make it json so lets get separate values
        obj_pairs = [x.split(":") for x in obj_pairs]
        # Now it looks like [(' type', ' related'), ]
        # and we need to clean up all the leading / trailing white space
        # and wrap each value in double quotes
        clean_pairs = []
        for pair in obj_pairs:
            clean_pairs.append(['"{}"'.format(p.strip()) for p in pair])
        # And join them together with colons
        colonized = [":".join(p) for p in clean_pairs]
        # So now colonized is ['"type":"stats"']
        # and we need to join those together with commas
        commas = ','.join(colonized)
        # And make it look like a JSON object...
        json_str = "{" + commas + "}"
        # And make it a python dictionary
        clean_objs.append(json.loads(json_str))
        
    # That was a lot of work! but now we can go get stats directly
    #double splat
    #keyword arg
    stats_url = (
        "http://goheels.com/services/responsive-roster-bio.ashx?"
        "type={type}&rp_id={rp_id}&path={path}&year={year}"
        "&player_id={player_id}"
    ).format(**clean_objs[0])
    
    
    resp = requests.get(stats_url, headers=headers)
    sel = scrapy.Selector(text=resp.content.decode('utf-8'))
    
    html = json.loads(resp.content.decode("utf-8"))["current_stats"]
    sel = scrapy.Selector(text=html)



In [143]:
sel

<Selector xpath=None data='<html><body><section>\r\n        <h5>Game-'>

In [144]:
clean_objs

[{'path': 'mbball',
  'player_id': '5167',
  'rp_id': '13524',
  'type': 'stats',
  'year': '2017'}]

In [145]:
stats_url = (
    "http://goheels.com/services/responsive-roster-bio.ashx?"
    "type={type}&rp_id={rp_id}&path={path}&year={year}"
    "&player_id={player_id}"
).format(**clean_objs[0])

In [146]:
resp = requests.get(stats_url, headers=headers)

In [147]:
body_str = body_bytes.decode('utf-8')

In [148]:
txt = resp.content.decode('utf-8')
#sel = scrapy.Selector(text=body_str)
sel = scrapy.Selector(text=txt)

In [149]:
resp.content

b'{"current_stats":"\\r\\n\\t\\t\\t\\t\\t\\r\\n    <section>\\r\\n        <h5>Game-By-Game Statistics</h5>\\r\\n\\r\\n        <div class=\\"sidearm-table-overflow-on-x-large\\">\\r\\n            <table class=\\"sidearm-table highlight-column-hover\\">\\r\\n                <caption class=\\"hide\\">Season Statistics</caption>\\r\\n                <thead>\\r\\n                    <tr>\\r\\n                        <th scope=\\"col\\" class=\\"text-left\\">Date</th>\\r\\n                        <th scope=\\"col\\" class=\\"text-left\\">Opponent</th>\\r\\n                        <th scope=\\"col\\">GS</th>\\r\\n                        <th scope=\\"col\\">MIN</th>\\r\\n                        <th scope=\\"col\\">FGM/A</th>\\r\\n                        <th scope=\\"col\\">%</th>\\r\\n                        <th scope=\\"col\\">3FG/A</th>\\r\\n                        <th scope=\\"col\\">%</th>\\r\\n                        <th scope=\\"col\\">FTM/A</th>\\r\\n                        <th scope=\\

In [150]:
html = json.loads(resp.content.decode("utf-8"))["current_stats"]

In [151]:
html

'\r\n\t\t\t\t\t\r\n    <section>\r\n        <h5>Game-By-Game Statistics</h5>\r\n\r\n        <div class="sidearm-table-overflow-on-x-large">\r\n            <table class="sidearm-table highlight-column-hover">\r\n                <caption class="hide">Season Statistics</caption>\r\n                <thead>\r\n                    <tr>\r\n                        <th scope="col" class="text-left">Date</th>\r\n                        <th scope="col" class="text-left">Opponent</th>\r\n                        <th scope="col">GS</th>\r\n                        <th scope="col">MIN</th>\r\n                        <th scope="col">FGM/A</th>\r\n                        <th scope="col">%</th>\r\n                        <th scope="col">3FG/A</th>\r\n                        <th scope="col">%</th>\r\n                        <th scope="col">FTM/A</th>\r\n                        <th scope="col">%</th>\r\n                        <th scope="col">OFF</th>\r\n                        <th scope="col">DEF</th>\r\n

In [152]:
# That looks better!

In [153]:
# scrape heels baseball
base_url = 'http://goheels.com'
url = base_url + '/roster.aspx?path=mbball'
resp = requests.get(url, headers=headers)
body_str = resp.content.decode('utf-8')
sel = scrapy.Selector(text=body_str)



table = sel.css('table')[0]



In [154]:
table

<Selector xpath='descendant-or-self::table' data='<table class="sidearm-table sidearm-tabl'>

In [155]:
#table.css('tr')[0].css('th').xpath('string()').extract()
table

<Selector xpath='descendant-or-self::table' data='<table class="sidearm-table sidearm-tabl'>

In [156]:
table

<Selector xpath='descendant-or-self::table' data='<table class="sidearm-table sidearm-tabl'>

In [157]:
cols = table.css('th').xpath('string()').extract()

In [158]:
cols

['No.', 'Name', 'Pos.', 'Ht.', 'Wt.', 'Yr.', 'Hometown / High School']

In [159]:
rows = table.css('tr')[1:]

In [160]:
rows

[<Selector xpath='descendant-or-self::tr' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                                  '>,
 <Selector xpath='descendant-or-self::tr' data='<tr>\r\n    

In [161]:
players = []
for r in rows:
    data = {}
    for i, d in enumerate(r.css('td')):
        a = d.css('a')
        if a:
            t = a.xpath('text()').extract()[0]
            data['href'] = a.xpath('@href').extract()[0]
        else:
            t = d.xpath('text()').extract()[0]
        data[cols[i]] = t
    players.append(data)

In [162]:
players

[{'Hometown / High School': 'Columbia, S.C. / Hammond School',
  'Ht.': '6-1',
  'Name': 'Seventh Woods',
  'No.': '0',
  'Pos.': 'G',
  'Wt.': '185',
  'Yr.': 'So.',
  'href': '/roster.aspx?rp_id=13521'},
 {'Hometown / High School': 'Greensboro, N.C. / Wesleyan Christian Academy',
  'Ht.': '6-6',
  'Name': 'Theo Pinson',
  'No.': '1',
  'Pos.': 'F/G',
  'Wt.': '220',
  'Yr.': 'Sr.',
  'href': '/roster.aspx?rp_id=13515'},
 {'Hometown / High School': 'Apopka, Fla. / Lake Highland Preparatory',
  'Ht.': '6-0',
  'Name': 'Joel Berry II',
  'No.': '2',
  'Pos.': 'G',
  'Wt.': '195',
  'Yr.': 'Sr.',
  'href': '/roster.aspx?rp_id=13508'},
 {'Hometown / High School': 'Guilderland, N.Y. / Northfield Mount Hermon School (Mass.)',
  'Ht.': '6-3',
  'Name': 'Andrew Platek',
  'No.': '3',
  'Pos.': 'G',
  'Wt.': '195',
  'Yr.': 'Fr.',
  'href': '/roster.aspx?rp_id=13528'},
 {'Hometown / High School': 'Douglasville, Ga. / Douglas County',
  'Ht.': '6-5',
  'Name': 'Brandon Robinson',
  'No.': '4',


In [163]:
players

[{'Hometown / High School': 'Columbia, S.C. / Hammond School',
  'Ht.': '6-1',
  'Name': 'Seventh Woods',
  'No.': '0',
  'Pos.': 'G',
  'Wt.': '185',
  'Yr.': 'So.',
  'href': '/roster.aspx?rp_id=13521'},
 {'Hometown / High School': 'Greensboro, N.C. / Wesleyan Christian Academy',
  'Ht.': '6-6',
  'Name': 'Theo Pinson',
  'No.': '1',
  'Pos.': 'F/G',
  'Wt.': '220',
  'Yr.': 'Sr.',
  'href': '/roster.aspx?rp_id=13515'},
 {'Hometown / High School': 'Apopka, Fla. / Lake Highland Preparatory',
  'Ht.': '6-0',
  'Name': 'Joel Berry II',
  'No.': '2',
  'Pos.': 'G',
  'Wt.': '195',
  'Yr.': 'Sr.',
  'href': '/roster.aspx?rp_id=13508'},
 {'Hometown / High School': 'Guilderland, N.Y. / Northfield Mount Hermon School (Mass.)',
  'Ht.': '6-3',
  'Name': 'Andrew Platek',
  'No.': '3',
  'Pos.': 'G',
  'Wt.': '195',
  'Yr.': 'Fr.',
  'href': '/roster.aspx?rp_id=13528'},
 {'Hometown / High School': 'Douglasville, Ga. / Douglas County',
  'Ht.': '6-5',
  'Name': 'Brandon Robinson',
  'No.': '4',


In [164]:
def fetch_bio(player):
    player_url = base_url + player['href']
    print('Fetch bio', player_url)
    resp = requests.get(player_url, headers=headers)
    player_txt = resp.content.decode('utf-8')
    sel = scrapy.Selector(text=player_txt)
    player['sel'] = sel
    player['bio'] = sel.css('#sidearm-roster-player-bio').xpath('string()').extract()[0]
    player['img'] = sel.css('.sidearm-roster-player-image img').xpath('@src').extract()[0]

In [165]:
js_obj_rx = re.compile(r'.*?responsive-roster-bio\.ashx.*?(?P<obj>{.*?})')

In [166]:
def fetch_stats(player):
    text = player['sel'].xpath('string()').extract()[0]
    parts = text.split('$.getJSON("/services/')[1:]
    captured = js_obj_rx.findall(''.join(parts))
    clean_objs = []
    for obj_str in captured:
        # We only want the stats object...
        if 'stats' not in obj_str:
            continue

        obj_str = obj_str.replace('{', '').replace('}', '')
        obj_str = obj_str.replace("'", '').replace('"', '')
        obj_pairs = obj_str.split(',')
        obj_pairs = [x.split(":") for x in obj_pairs]
        clean_pairs = []
        for pair in obj_pairs:
            clean_pairs.append(['"{}"'.format(p.strip()) for p in pair])
        colonized = [":".join(p) for p in clean_pairs]
        commas = ','.join(colonized)
        json_str = "{" + commas + "}"
        clean_objs.append(json.loads(json_str))
    
    player['stats_url'] = stats_url = (
        "http://goheels.com/services/responsive-roster-bio.ashx?"
        "type={type}&rp_id={rp_id}&path={path}&year={year}"
        "&player_id={player_id}"
    ).format(**clean_objs[0])
    
    print('Fetch stats', stats_url)
    resp = requests.get(stats_url, headers=headers)
    json_stats = json.loads(resp.content.decode("utf-8"))
    player['raw_stats'] = json_stats

In [167]:
for p in players:
    fetch_bio(p)
    fetch_stats(p)

Fetch bio http://goheels.com/roster.aspx?rp_id=13521
Fetch stats http://goheels.com/services/responsive-roster-bio.ashx?type=stats&rp_id=13521&path=mbball&year=2017&player_id=4736
Fetch bio http://goheels.com/roster.aspx?rp_id=13515
Fetch stats http://goheels.com/services/responsive-roster-bio.ashx?type=stats&rp_id=13515&path=mbball&year=2017&player_id=4636
Fetch bio http://goheels.com/roster.aspx?rp_id=13508
Fetch stats http://goheels.com/services/responsive-roster-bio.ashx?type=stats&rp_id=13508&path=mbball&year=2017&player_id=4632
Fetch bio http://goheels.com/roster.aspx?rp_id=13528
Fetch stats http://goheels.com/services/responsive-roster-bio.ashx?type=stats&rp_id=13528&path=mbball&year=2017&player_id=5171
Fetch bio http://goheels.com/roster.aspx?rp_id=13516
Fetch stats http://goheels.com/services/responsive-roster-bio.ashx?type=stats&rp_id=13516&path=mbball&year=2017&player_id=4733
Fetch bio http://goheels.com/roster.aspx?rp_id=13518
Fetch stats http://goheels.com/services/respons

In [168]:
players[0]

{'Hometown / High School': 'Columbia, S.C. / Hammond School',
 'Ht.': '6-1',
 'Name': 'Seventh Woods',
 'No.': '0',
 'Pos.': 'G',
 'Wt.': '185',
 'Yr.': 'So.',
 'bio': '\r\n                        Biography\r\n                                                    \r\n                            FRESHMAN SEASON (2016-17)\r\n\r\nTied a school record by appearing in all 40 games • Averaged 7.7 minutes per game in the primary relief role behind Joel Berry II at the point • Had 49 assists, 42 turnovers and 21 steals • Had 25 assists and 13 turnovers in ACC regular-season play • Made two steals five times • Was on the floor for five minutes vs. Louisville as UNC out-scored the Cards, 10-2 • Played his bestgame in conference play at Duke when he scored four points and had a team-high four assists in eight minutes • Played a seven and a half minute stretch in the first half as UNC cut Duke’s lead from three to one • Was the first time he led UNC in assists since Long Beach State on 11/15 • Had t

In [169]:
#p = [p for p in players if p['Name'] == 'Seventh Woods'][0]

In [170]:
txt = p['raw_stats']['career_stats']


In [171]:
sel = scrapy.Selector(text=txt)


In [172]:
sel.css('section')


[]

In [173]:
#[x.pop('stats') for x in players]

In [174]:
def parse_stats(player):
    stats = {}
    for raw_key, raw_val in player['raw_stats'].items():
        txt = player['raw_stats'][raw_key]
        if not txt:
            print('Skipping {} for {}'.format(raw_key, player['Name']))
            continue
        sel = scrapy.Selector(text=txt)
        # Get all the tables
        for section in sel.css('section'):
            title = section.css('h5').xpath('string()').extract()[0]
            cols = section.css('tr')[0].css('th').xpath('string()').extract()
            print('NEW SECTION', title)
            print('COLS', cols)
            these_stats = []
            print('TRS', section.css('tr'))
            for r in section.css('tr')[1:]:
                print('row', r.xpath('string()').extract()[0].replace('\r', '').replace('\n', '').strip())
                s = {}
                for i, d in enumerate(r.css('td'), 0):
                    s[cols[i].lower()] = d.xpath('string()').extract()[0]
                yr = r.css('th').xpath('string()')
                if yr:
                    yr = yr.extract()[0]
                    if yr.lower() in ('total', 'season'):
                        print('SKIPPING...')
                        continue
                    print('THE YEAR IS', yr)
                    s['year'] = yr
                these_stats.append(s)
                print('THE STATS ARE', these_stats)
            existing = stats.get(raw_key, {})
            existing[title] = these_stats
            stats[raw_key] = existing
    player['stats'] = stats

In [175]:
#p = [p for p in players if p['Name'] == 'Seventh Woods'][0]
for p in players:
    parse_stats(p)

NEW SECTION Game-By-Game Statistics
COLS ['Date', 'Opponent', 'GS', 'MIN', 'FGM/A', '%', '3FG/A', '%', 'FTM/A', '%', 'OFF', 'DEF', 'TOT', 'AVG', 'PF', 'AST', 'T/O', 'BLK', 'STL', 'PTS', 'AVG']
TRS [<Selector xpath='descendant-or-self::tr' data='<tr>\r\n                        <th scope='>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>       

THE STATS ARE [{'date': '11/10/17', 'opponent': '*', 'gs': '26', 'min': '1-6', 'fgm/a': '.167', '%': '0', '3fg/a': '.167', 'ftm/a': '.000', 'off': '3', 'def': '3', 'tot': '3.0', 'avg': '1', 'pf': '5', 'ast': '0', 't/o': '0', 'blk': '0', 'stl': '3', 'pts': '3.0', 'year': ' Northern Iowa'}, {'date': '11/15/17', 'opponent': '*', 'gs': '33', 'min': '5-12', 'fgm/a': '.417', '%': '0', '3fg/a': '.000', 'ftm/a': '.900', 'off': '5', 'def': '5', 'tot': '4.0', 'avg': '3', 'pf': '6', 'ast': '2', 't/o': '0', 'blk': '1', 'stl': '19', 'pts': '11.0', 'year': ' Bucknell'}, {'date': '11/20/17', 'opponent': '*', 'gs': '29', 'min': '4-8', 'fgm/a': '.500', '%': '1', '3fg/a': '.000', 'ftm/a': '.500', 'off': '4', 'def': '5', 'tot': '4.3', 'avg': '1', 'pf': '2', 'ast': '2', 't/o': '0', 'blk': '0', 'stl': '9', 'pts': '10.3', 'year': 'at STANFORD'}, {'date': '11/23/17', 'opponent': '*', 'gs': '25', 'min': '4-7', 'fgm/a': '.571', '%': '2', '3fg/a': '.333', 'ftm/a': '.500', 'off': '7', 'def': '9', 'tot': '5.5', '

THE YEAR IS  Notre Dame
THE STATS ARE [{'date': '11/15/17', 'opponent': '*', 'gs': '30', 'min': '1-11', 'fgm/a': '.091', '%': '1', '3fg/a': '.200', 'ftm/a': '.833', 'off': '3', 'def': '4', 'tot': '4.0', 'avg': '2', 'pf': '6', 'ast': '1', 't/o': '0', 'blk': '2', 'stl': '8', 'pts': '8.0', 'year': ' Bucknell'}, {'date': '11/20/17', 'opponent': '*', 'gs': '30', 'min': '10-19', 'fgm/a': '.526', '%': '1', '3fg/a': '.455', 'ftm/a': '1.000', 'off': '0', 'def': '1', 'tot': '2.5', 'avg': '2', 'pf': '3', 'ast': '2', 't/o': '0', 'blk': '0', 'stl': '29', 'pts': '18.5', 'year': 'at STANFORD'}, {'date': '11/23/17', 'opponent': '*', 'gs': '26', 'min': '6-14', 'fgm/a': '.429', '%': '0', '3fg/a': '.444', 'ftm/a': '1.000', 'off': '3', 'def': '3', 'tot': '2.7', 'avg': '0', 'pf': '2', 'ast': '0', 't/o': '0', 'blk': '1', 'stl': '18', 'pts': '18.3', 'year': 'vs Portland'}, {'date': '11/24/17', 'opponent': '*', 'gs': '34', 'min': '3-12', 'fgm/a': '.250', '%': '0', '3fg/a': '.000', 'ftm/a': '.875', 'off': '2',

row 01/20/18                             Georgia Tech                                                        4                            0-0                            .000                            0-0                            .000                            0-0                            .000                            1                            2                            3                            1.2                            0                            0                            0                            0                            1                            0                            2.3
THE YEAR IS  Georgia Tech
THE STATS ARE [{'date': '11/10/17', 'opponent': '', 'gs': '10', 'min': '1-1', 'fgm/a': '1.000', '%': '0', '3fg/a': '.000', 'ftm/a': '1.000', 'off': '0', 'def': '0', 'tot': '0.0', 'avg': '0', 'pf': '0', 'ast': '0', 't/o': '0', 'blk': '0', 'stl': '4', 'pts': '4.0', 'year': ' Northern Iowa'}, {'date': '11/15/17', 'opponent': '', 'gs': '14', 'min': '0-1

row 02/08/18                             Duke                                                        6                            0-3                            .000                            0-1                            .000                            0-0                            .000                            1                            0                            1                            1.7                            1                            0                            0                            1                            0                            0                            2.2
THE YEAR IS  Duke
THE STATS ARE [{'date': '11/10/17', 'opponent': '', 'gs': '16', 'min': '0-2', 'fgm/a': '.000', '%': '0', '3fg/a': '.000', 'ftm/a': '1.000', 'off': '2', 'def': '2', 'tot': '2.0', 'avg': '1', 'pf': '3', 'ast': '0', 't/o': '0', 'blk': '0', 'stl': '2', 'pts': '2.0', 'year': ' Northern Iowa'}, {'date': '11/23/17', 'opponent': '', 'gs': '12', 'min': '1-4', 'fgm/a': '.250

...

row Free Throw Attempts                        6                        vs. Duke
THE STATS ARE [{'statistic': 'Points', 'value': '14', 'opponent': 'vs. Northern Iowa'}, {'statistic': 'Minutes', 'value': '24', 'opponent': 'vs. Wofford'}, {'statistic': 'Field Goals Made', 'value': '5', 'opponent': 'vs. Pittsburgh'}, {'statistic': 'Field Goal Attempts', 'value': '7', 'opponent': 'vs. Duke'}, {'statistic': '3-Point Field Goals Made', 'value': '0', 'opponent': 'vs. Texas A&M'}, {'statistic': '3-Point Field Goal Attempts', 'value': '0', 'opponent': 'vs. Texas A&M'}, {'statistic': 'Free Throws Made', 'value': '4', 'opponent': 'vs. Duke'}, {'statistic': 'Free Throw Attempts', 'value': '6', 'opponent': 'vs. Duke'}]
row Rebounds                        8                        vs. Tennessee
THE STATS ARE [{'statistic': 'Points', 'value': '14', 'opponent': 'vs. Northern Iowa'}, {'statistic': 'Minutes', 'value': '24', 'opponent': 'vs. Wofford'}, {'statistic': 'Field Goals Made', 'value': '5', 'oppo

row 11/23/17                            vs Portland                                                        2                            0-0                            .000                            0-0                            .000                            0-0                            .000                            0                            0                            0                            0.3                            0                            1                            0                            1                            0                            0                            0.0
THE YEAR IS vs Portland
THE STATS ARE [{'date': '11/10/17', 'opponent': '', 'gs': '5', 'min': '0-2', 'fgm/a': '.000', '%': '0', '3fg/a': '.000', 'ftm/a': '.000', 'off': '0', 'def': '0', 'tot': '0.0', 'avg': '2', 'pf': '1', 'ast': '0', 't/o': '0', 'blk': '0', 'stl': '0', 'pts': '0.0', 'year': ' Northern Iowa'}, {'date': '11/20/17', 'opponent': '', 'gs': '2', 'min': '0-0', 'fgm/

row 01/13/18                            at Notre Dame                            *                            28                            2-7                            .286                            0-3                            .000                            1-3                            .333                            1                            2                            3                            3.4                            5                            3                            2                            1                            2                            5                            12.1
THE YEAR IS at Notre Dame
THE STATS ARE [{'date': '11/10/17', 'opponent': '*', 'gs': '28', 'min': '3-8', 'fgm/a': '.375', '%': '0', '3fg/a': '.500', 'ftm/a': '1.000', 'off': '1', 'def': '1', 'tot': '1.0', 'avg': '2', 'pf': '5', 'ast': '1', 't/o': '0', 'blk': '3', 'stl': '10', 'pts': '10.0', 'year': ' Northern Iowa'}, {'date': '11/15/17', 'opponent': '*', 'gs': '29', 'min'

THE YEAR IS  Northern Iowa
THE STATS ARE [{'date': '11/10/17', 'opponent': '*', 'gs': '28', 'min': '11-16', 'fgm/a': '.688', '%': '3', '3fg/a': '.667', 'ftm/a': '1.000', 'off': '7', 'def': '10', 'tot': '10.0', 'avg': '2', 'pf': '0', 'ast': '1', 't/o': '1', 'blk': '1', 'stl': '26', 'pts': '26.0', 'year': ' Northern Iowa'}]
row 11/15/17                             Bucknell                            *                            37                            6-12                            .500                            3-4                            .750                            5-8                            .625                            1                            8                            9                            9.5                            4                            4                            1                            2                            1                            20                            23.0
THE YEAR IS  Bucknell
THE STATS ARE [{'date': '11/10

THE YEAR IS vs Arkansas
THE STATS ARE [{'date': '11/10/17', 'opponent': '', 'gs': '9', 'min': '2-4', 'fgm/a': '.500', '%': '0', '3fg/a': '.000', 'ftm/a': '.000', 'off': '1', 'def': '1', 'tot': '1.0', 'avg': '2', 'pf': '0', 'ast': '0', 't/o': '0', 'blk': '0', 'stl': '4', 'pts': '4.0', 'year': ' Northern Iowa'}, {'date': '11/15/17', 'opponent': '', 'gs': '4', 'min': '2-2', 'fgm/a': '1.000', '%': '1', '3fg/a': '.000', 'ftm/a': '.000', 'off': '1', 'def': '2', 'tot': '1.5', 'avg': '1', 'pf': '0', 'ast': '0', 't/o': '1', 'blk': '0', 'stl': '4', 'pts': '4.0', 'year': ' Bucknell'}, {'date': '11/20/17', 'opponent': '', 'gs': '9', 'min': '2-2', 'fgm/a': '1.000', '%': '1', '3fg/a': '.000', 'ftm/a': '1.000', 'off': '4', 'def': '5', 'tot': '2.7', 'avg': '4', 'pf': '0', 'ast': '0', 't/o': '0', 'blk': '0', 'stl': '8', 'pts': '5.3', 'year': 'at STANFORD'}, {'date': '11/23/17', 'opponent': '', 'gs': '9', 'min': '2-4', 'fgm/a': '.500', '%': '3', '3fg/a': '.000', 'ftm/a': '.500', 'off': '0', 'def': '3', 

In [176]:
for p in players:
    parse_stats(p)

NEW SECTION Game-By-Game Statistics
COLS ['Date', 'Opponent', 'GS', 'MIN', 'FGM/A', '%', '3FG/A', '%', 'FTM/A', '%', 'OFF', 'DEF', 'TOT', 'AVG', 'PF', 'AST', 'T/O', 'BLK', 'STL', 'PTS', 'AVG']
TRS [<Selector xpath='descendant-or-self::tr' data='<tr>\r\n                        <th scope='>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>                        \r\n          '>, <Selector xpath='descendant-or-self::tr' data='<tr>       

THE STATS ARE [{'date': '11/10/17', 'opponent': '', 'gs': '18', 'min': '3-6', 'fgm/a': '.500', '%': '0', '3fg/a': '.000', 'ftm/a': '.750', 'off': '0', 'def': '0', 'tot': '0.0', 'avg': '2', 'pf': '2', 'ast': '1', 't/o': '0', 'blk': '2', 'stl': '9', 'pts': '9.0', 'year': ' Northern Iowa'}, {'date': '11/15/17', 'opponent': '', 'gs': '10', 'min': '1-2', 'fgm/a': '.500', '%': '0', '3fg/a': '.000', 'ftm/a': '.000', 'off': '2', 'def': '2', 'tot': '1.0', 'avg': '1', 'pf': '1', 'ast': '1', 't/o': '0', 'blk': '0', 'stl': '2', 'pts': '5.5', 'year': ' Bucknell'}, {'date': '11/20/17', 'opponent': '', 'gs': '12', 'min': '1-4', 'fgm/a': '.250', '%': '0', '3fg/a': '.000', 'ftm/a': '.000', 'off': '2', 'def': '2', 'tot': '1.3', 'avg': '0', 'pf': '1', 'ast': '1', 't/o': '0', 'blk': '1', 'stl': '2', 'pts': '4.3', 'year': 'at STANFORD'}, {'date': '11/23/17', 'opponent': '', 'gs': '14', 'min': '0-3', 'fgm/a': '.000', '%': '0', '3fg/a': '.000', 'ftm/a': '.000', 'off': '4', 'def': '4', 'tot': '2.0', 'avg': '1

row 01/16/18                             Clemson                            *                            31                            2-7                            .286                            0-4                            .000                            8-8                            1.000                            0                            7                            7                            5.3                            4                            6                            2                            3                            1                            12                            9.1
THE YEAR IS  Clemson
THE STATS ARE [{'date': '11/10/17', 'opponent': '*', 'gs': '26', 'min': '1-6', 'fgm/a': '.167', '%': '0', '3fg/a': '.167', 'ftm/a': '.000', 'off': '3', 'def': '3', 'tot': '3.0', 'avg': '1', 'pf': '5', 'ast': '0', 't/o': '0', 'blk': '0', 'stl': '3', 'pts': '3.0', 'year': ' Northern Iowa'}, {'date': '11/15/17', 'opponent': '*', 'gs': '33', 'min': '5-12', 'f

THE YEAR IS vs Syracuse
THE STATS ARE [{'date': '11/10/17', 'opponent': '*', 'gs': '26', 'min': '1-6', 'fgm/a': '.167', '%': '0', '3fg/a': '.167', 'ftm/a': '.000', 'off': '3', 'def': '3', 'tot': '3.0', 'avg': '1', 'pf': '5', 'ast': '0', 't/o': '0', 'blk': '0', 'stl': '3', 'pts': '3.0', 'year': ' Northern Iowa'}, {'date': '11/15/17', 'opponent': '*', 'gs': '33', 'min': '5-12', 'fgm/a': '.417', '%': '0', '3fg/a': '.000', 'ftm/a': '.900', 'off': '5', 'def': '5', 'tot': '4.0', 'avg': '3', 'pf': '6', 'ast': '2', 't/o': '0', 'blk': '1', 'stl': '19', 'pts': '11.0', 'year': ' Bucknell'}, {'date': '11/20/17', 'opponent': '*', 'gs': '29', 'min': '4-8', 'fgm/a': '.500', '%': '1', '3fg/a': '.000', 'ftm/a': '.500', 'off': '4', 'def': '5', 'tot': '4.3', 'avg': '1', 'pf': '2', 'ast': '2', 't/o': '0', 'blk': '0', 'stl': '9', 'pts': '10.3', 'year': 'at STANFORD'}, {'date': '11/23/17', 'opponent': '*', 'gs': '25', 'min': '4-7', 'fgm/a': '.571', '%': '2', '3fg/a': '.333', 'ftm/a': '.500', 'off': '7', 'de

row 02/17/18                            at LOUISVILLE                            *                            36                            9-20                            .450                            5-11                            .455                            0-0                            .000                            1                            7                            8                            3.8                            1                            5                            2                            1                            1                            23                            17.7
THE YEAR IS at LOUISVILLE
THE STATS ARE [{'date': '11/15/17', 'opponent': '*', 'gs': '30', 'min': '1-11', 'fgm/a': '.091', '%': '1', '3fg/a': '.200', 'ftm/a': '.833', 'off': '3', 'def': '4', 'tot': '4.0', 'avg': '2', 'pf': '6', 'ast': '1', 't/o': '0', 'blk': '2', 'stl': '8', 'pts': '8.0', 'year': ' Bucknell'}, {'date': '11/20/17', 'opponent': '*', 'gs': '30', 'min': '1

...

THE YEAR IS  Duke
THE STATS ARE [{'date': '11/10/17', 'opponent': '*', 'gs': '28', 'min': '3-8', 'fgm/a': '.375', '%': '0', '3fg/a': '.500', 'ftm/a': '1.000', 'off': '1', 'def': '1', 'tot': '1.0', 'avg': '2', 'pf': '5', 'ast': '1', 't/o': '0', 'blk': '3', 'stl': '10', 'pts': '10.0', 'year': ' Northern Iowa'}, {'date': '11/15/17', 'opponent': '*', 'gs': '29', 'min': '4-7', 'fgm/a': '.571', '%': '1', '3fg/a': '.500', 'ftm/a': '.000', 'off': '0', 'def': '1', 'tot': '1.0', 'avg': '4', 'pf': '2', 'ast': '3', 't/o': '1', 'blk': '2', 'stl': '10', 'pts': '10.0', 'year': ' Bucknell'}, {'date': '11/20/17', 'opponent': '*', 'gs': '31', 'min': '7-11', 'fgm/a': '.636', '%': '1', '3fg/a': '.750', 'ftm/a': '.000', 'off': '3', 'def': '4', 'tot': '2.0', 'avg': '1', 'pf': '3', 'ast': '1', 't/o': '0', 'blk': '1', 'stl': '20', 'pts': '13.3', 'year': 'at STANFORD'}, {'date': '11/23/17', 'opponent': '*', 'gs': '25', 'min': '7-12', 'fgm/a': '.583', '%': '3', '3fg/a': '.333', 'ftm/a': '1.000', 'off': '0', 'de

row 01/20/18                             Georgia Tech                                                        1                            0-0                            .000                            0-0                            .000                            0-0                            .000                            0                            0                            0                            0.5                            0                            0                            0                            0                            0                            0                            0.3
THE YEAR IS  Georgia Tech
THE STATS ARE [{'date': '11/10/17', 'opponent': '', 'gs': '2', 'min': '0-0', 'fgm/a': '.000', '%': '0', '3fg/a': '.000', 'ftm/a': '.000', 'off': '2', 'def': '2', 'tot': '2.0', 'avg': '0', 'pf': '0', 'ast': '0', 't/o': '0', 'blk': '0', 'stl': '0', 'pts': '0.0', 'year': ' Northern Iowa'}, {'date': '11/20/17', 'opponent': '', 'gs': '2', 'min': '1-1', '

NEW SECTION Season Highs
COLS ['Statistic', 'Value', 'Opponent']
TRS [<Selector xpath='descendant-or-self::tr' data='<tr>\r\n                    <th class="tex'>, <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                        <td>Points'>, <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                        <td>Minute'>, <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                        <td>Field '>, <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                        <td>Field '>, <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                        <td>3-Poin'>, <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                        <td>3-Poin'>, <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                        <td>Free T'>, <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                        <td>Free T'>, <Selector xpath='descendant-or-self::tr' data='<tr>\r\n                        <td>Reboun'>, 

row 02/27/18                             Miami                            *                            34                            6-10                            .600                            1-3                            .333                            1-2                            .500                            3                            7                            10                            10.2                            3                            0                            2                            0                            0                            14                            17.9
THE YEAR IS  Miami
THE STATS ARE [{'date': '11/10/17', 'opponent': '*', 'gs': '28', 'min': '11-16', 'fgm/a': '.688', '%': '3', '3fg/a': '.667', 'ftm/a': '1.000', 'off': '7', 'def': '10', 'tot': '10.0', 'avg': '2', 'pf': '0', 'ast': '1', 't/o': '1', 'blk': '1', 'stl': '26', 'pts': '26.0', 'year': ' Northern Iowa'}, {'date': '11/15/17', 'opponent': '*', 'gs': '37', 'min': '6-1

THE STATS ARE [{'statistic': 'Points', 'value': '33', 'opponent': 'vs. North Carolina State'}, {'statistic': 'Minutes', 'value': '37', 'opponent': 'vs. North Carolina State'}, {'statistic': 'Field Goals Made', 'value': '15', 'opponent': 'vs. North Carolina State'}, {'statistic': 'Field Goal Attempts', 'value': '23', 'opponent': 'vs. North Carolina State'}, {'statistic': '3-Point Field Goals Made', 'value': '4', 'opponent': 'vs. Virginia'}, {'statistic': '3-Point Field Goal Attempts', 'value': '7', 'opponent': 'vs. Virginia'}, {'statistic': 'Free Throws Made', 'value': '7', 'opponent': 'vs. Wofford'}, {'statistic': 'Free Throw Attempts', 'value': '9', 'opponent': 'vs. Tulane'}, {'statistic': 'Rebounds', 'value': '18', 'opponent': 'vs. Boston College'}]
row Assists                        5                        vs. Pittsburgh
THE STATS ARE [{'statistic': 'Points', 'value': '33', 'opponent': 'vs. North Carolina State'}, {'statistic': 'Minutes', 'value': '37', 'opponent': 'vs. North Carol

In [177]:

to_dump = [p.copy() for p in players]
for p in to_dump:
    p.pop('sel')
    for k in list(p.keys()):
        if 'raw' in k:
            p.pop(k)
with open('scraped_players.json', 'w') as f:
    json.dump(to_dump, f)

In [178]:
cat scraped_players.json | cut -c 1-100

[{"No.": "0", "href": "/roster.aspx?rp_id=13521", "Name": "Seventh Woods", "Pos.": "G", "Ht.": "6-1"


In [179]:
to_dump[0]

{'Hometown / High School': 'Columbia, S.C. / Hammond School',
 'Ht.': '6-1',
 'Name': 'Seventh Woods',
 'No.': '0',
 'Pos.': 'G',
 'Wt.': '185',
 'Yr.': 'So.',
 'bio': '\r\n                        Biography\r\n                                                    \r\n                            FRESHMAN SEASON (2016-17)\r\n\r\nTied a school record by appearing in all 40 games • Averaged 7.7 minutes per game in the primary relief role behind Joel Berry II at the point • Had 49 assists, 42 turnovers and 21 steals • Had 25 assists and 13 turnovers in ACC regular-season play • Made two steals five times • Was on the floor for five minutes vs. Louisville as UNC out-scored the Cards, 10-2 • Played his bestgame in conference play at Duke when he scored four points and had a team-high four assists in eight minutes • Played a seven and a half minute stretch in the first half as UNC cut Duke’s lead from three to one • Was the first time he led UNC in assists since Long Beach State on 11/15 • Had t

In [180]:
df = pd.read_json("scraped_players.json")
df.columns

Index(['Hometown / High School', 'Ht.', 'Name', 'No.', 'Pos.', 'Wt.', 'Yr.',
       'bio', 'href', 'img', 'stats', 'stats_url'],
      dtype='object')

In [181]:
df


Hometown / High School   Ht.              Name  \
0                     Columbia, S.C. / Hammond School   6-1     Seventh Woods   
1       Greensboro, N.C. / Wesleyan Christian Academy   6-6       Theo Pinson   
2            Apopka, Fla. / Lake Highland Preparatory   6-0     Joel Berry II   
3   Guilderland, N.Y. / Northfield Mount Hermon Sc...   6-3     Andrew Platek   
4                  Douglasville, Ga. / Douglas County   6-5  Brandon Robinson   
5   Fairway, Kan. / The Barstow School (Kansas Cit...   6-5         Shea Rush   
6   Moon Township, Pa. / Our Lady of the Sacred He...   6-8   Cameron Johnson   
7        Greensboro, N.C. / New Garden Friends School   6-0           Kane Ma   
8                            Lafayette, Ala. / Auburn   6-9   Garrison Brooks   
9           Pickerington, Ohio / Pickerington Central  6-11   Sterling Manley   
10         Greensboro, N.C. / New Hampton Prep (N.H.)  6-10     Walker Miller   
11                             Midlothian, Va. / Bird   6-4    Kenny Williams   
12                       Gastonia, N.C. / Hunter Huss   6-6     Aaron Rohlman   
13  Calabasas, Calif. / IMG Academy (Bradenton, Fla.)   6-2        K.J. Smith   
14                         Huntersville, N.C. / Hough   6-8         Luke Maye   
15    Goldsboro, N.C. / Word of God Christian Academy  6-10   Brandon Huffman   

    No. Pos.  Wt.  Yr.                                                bio  \
0     0    G  185  So.  \r\n                        Biography\r\n     ...   
1     1  F/G  220  Sr.  \r\n                        Biography\r\n     ...   
2     2    G  195  Sr.  \r\n                        Biography\r\n     ...   
3     3    G  195  Fr.  \r\n                        Biography\r\n     ...   
4     4    G  170  So.  \r\n                        Biography\r\n     ...   
5    11    F  210  So.  \r\n                        Biography\r\n     ...   
6    13    G  210  Gr.  \r\n                        Biography\r\n     ...   
7    14    G  175  Sr.  \r\n                        Biography\r\n     ...   
8    15    F  215  Fr.  \r\n                        Biography\r\n     ...   
9    21    F  240  Fr.  \r\n                        Biography\r\n     ...   
10   22    F  220  Fr.  \r\n                        Biography\r\n     ...   
11   24    G  185  Jr.  \r\n                        Biography\r\n     ...   
12   25    F  210  Sr.  \r\n                        Biography\r\n     ...   
13   30    G  180  So.  \r\n                        Biography\r\n     ...   
14   32    F  240  Jr.  \r\n                        Biography\r\n     ...   
15   42    F  250  Fr.  \r\n                        Biography\r\n     ...   

                        href  \
0   /roster.aspx?rp_id=13521   
1   /roster.aspx?rp_id=13515   
2   /roster.aspx?rp_id=13508   
3   /roster.aspx?rp_id=13528   
4   /roster.aspx?rp_id=13516   
5   /roster.aspx?rp_id=13518   
6   /roster.aspx?rp_id=13525   
7   /roster.aspx?rp_id=14170   
8   /roster.aspx?rp_id=13522   
9   /roster.aspx?rp_id=13526   
10  /roster.aspx?rp_id=13527   
11  /roster.aspx?rp_id=13520   
12  /roster.aspx?rp_id=13517   
13  /roster.aspx?rp_id=13530   
14  /roster.aspx?rp_id=13513   
15  /roster.aspx?rp_id=13524   

                                                  img  \
0   /images/2017/9/12/Woods_Seventh_mb_2017_181.jp...   
1   /images/2017/9/12/Pinson_Theo_mb_2017_23.jpg?w...   
2   /images/2017/9/12/Berry_Joel_mb_2017_59.jpg?wi...   
3   /images/2017/9/12/Platek_Andrew_mb_2017_211.jp...   
4   /images/2017/9/12/Robinson_Brandon_mb_2017_122...   
5          /images/2017/12/22/Rush_Shea.jpg?width=300   
6   /images/2017/9/12/Johnson_Cameron_mb_2017_130....   
7            /images/2017/12/22/Ma_Kane.jpg?width=300   
8   /images/2017/9/12/Brooks_Garrison_mb_2017_221....   
9   /images/2017/9/12/Manley_Sterling_mb_2017_106....   
10  /images/2017/9/12/Miller_Walker_mb_2017_39.jpg...   
11  /images/2017/9/12/Williams_Kenny_mb_2017_90.jp...   
12  /images/2017/9/12/Rohlman_Aaron_mb_2017_217.jp...   


In [183]:
#df = df.set_index["Name"]

In [184]:
grouped = df.groupby("Yr.")
type(grouped)
grouped.groups

{'Fr.': Int64Index([3, 8, 9, 10, 15], dtype='int64'),
 'Gr.': Int64Index([6], dtype='int64'),
 'Jr.': Int64Index([11, 14], dtype='int64'),
 'So.': Int64Index([0, 4, 5, 13], dtype='int64'),
 'Sr.': Int64Index([1, 2, 7, 12], dtype='int64')}